In [1]:
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx
import pandas as pd
import sklearn
import re
import itertools
import datetime
from sklearn import metrics
from sklearn.metrics import r2_score, mean_squared_error, f1_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.model_selection import train_test_split


In [2]:
def convertDate(date):
    dates = date.split("-")
    convert = datetime.date(int(dates[0]), int(dates[1]), int(dates[2]))
    return convert

def getThread(num,data):
    thread = data[data["ThreadID"]== threads[num]]
    members = thread["MemberID"].unique()
    thread = thread.reset_index(drop = True)
    
    for i in range(0,len(thread)):
        thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
    
    #encode member names
    index = 0
    for i in range(0,len(members)):
        thread["MemberID"][thread["MemberID"] == members[i]] = index
        index += 1

    thread = thread.sort_values(by = ["P_Date",'MessageID'])
    
    return thread

In [3]:
def makeGraph(thread):
    members = thread["MemberID"].unique()
    memberComments = []
    memberSentiments = []

    for i in members:
        memberComments.append(len(thread[thread["MemberID"] == i]))
        memberSentiments.append(thread[thread["MemberID"] == i]["AllenNLP"].iloc[-1])

    #Make graph
    #Make dictionary of nodes (members) with corresponding mean sentiment of that member
    nodes = np.array(members,dtype = int)
    nodeDict = dict(zip(nodes,np.around(memberSentiments,4)))

    edges = []
    for i in range(0,len(thread)-1):
        if thread["MemberID"].iloc[i] != thread["MemberID"].iloc[i +1]:
            edge = (tuple([int(thread["MemberID"].iloc[i]),int(thread["MemberID"].iloc[i+1])]))
            edges.append(edge)

    sortEdges = [np.sort(x) for x in edges]
    edgeKeys = np.unique(sortEdges,axis=0)
    edgeValues = []

    for i in range(0,len(edgeKeys)):
        count = 0
        for j in range(0,len(sortEdges)):
            count += np.array_equal(sortEdges[j],edgeKeys[i])
        edgeValues.append(count)

    edgeKeys=[tuple(edgeKeys.tolist()[x]) for x in range(0,len(edgeKeys))]
    edgeDict = dict(zip(edgeKeys,edgeValues))

    G = nx.Graph()
    G.add_nodes_from(nodes)
    G.add_edges_from(edges)
    
    centrality = nx.information_centrality(G) #nx.pagerank(G)
    
    return G, nodeDict, edgeDict, centrality

### Create Graphs

In [4]:
data = pd.read_csv("../GawaherSentiment.csv")
threads = data["ThreadID"].unique()


### Get Features

In [5]:
connectedSentiment = []
connectedCentralities = []
targetCentralities = []
values = []
edges = []
ThreadID = []

for i in range(0,len(threads)):
    thread = getThread(i,data)
    G, nodeDict, edgeDict, centrality = makeGraph(thread)
    for j in nodeDict.keys():
        connectedNodes = list(G.neighbors(j))
        connectedValues = [nodeDict[x] for x in connectedNodes]
        connectedEdge = [edgeDict[tuple(np.sort([j,x]))] for x in connectedNodes]
        connectedCentrality =  [centrality[x] for x in connectedNodes]
        targetCentrality = np.full(len(connectedValues),centrality[j])
        targetValues = np.full(len(connectedValues),nodeDict[j])
        
        connectedSentiment.append(connectedValues)
        edges.append(connectedEdge)
        connectedCentralities.append(connectedCentrality)
        targetCentralities.append( targetCentrality)
        ThreadID.append(np.full(len(connectedValues),threads[i]))
        values.append(targetValues)

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

...

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-v

In [6]:
features = pd.DataFrame(np.array([np.concatenate(ThreadID),
                         np.concatenate(connectedSentiment),
                         np.concatenate(edges),
                         np.concatenate(connectedCentralities),
                         np.concatenate(targetCentralities),
                         np.sign(np.concatenate(values))]).T,
                         columns = ["threadID","connectedSentiment","edges","connectedCentrality","targetCentrality","values"])
features.dropna(inplace=True)


positive = features[features["values"] > 0]
negative = features[features["values"] < 0].sample(frac=1)[:len(positive)]
features = pd.concat([negative,positive])

In [7]:
threads = np.random.choice(threads, len(threads))

trainThreads = threads[:int(.8*len(threads))]
testThreads =  threads[int(.8*len(threads)):]

In [8]:
mask = features["threadID"].isin(trainThreads)


In [9]:
features = features.sample(frac = 1)
x = features[features.columns[1:-1]]
y = features[features.columns[-1]]

In [10]:
xTrain = x[mask]
yTrain = y[mask]

xTest = x[~mask]
yTest = y[~mask]

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2121947701.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  xTrain = x[mask]
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2121947701.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  xTest = x[~mask]


synthData = pd.read_csv("syntheticData.csv")

xSynth =synthData[features.columns[1:-1]]
ySynth =synthData[features.columns[-1]]

In [11]:
clf = RandomForestClassifier(n_jobs = -1)
clf = clf.fit(xTrain, yTrain)
clf.score(xTest,yTest)

0.5899363591859571

### Test Classifier

In [12]:
def classify(target,G,nodeDict,edgeDict,centrality, classifier):
    connectedNodes = list(G.neighbors(target))
    connectedValues = [nodeDict[x] for x in connectedNodes]
    connectedEdge = [edgeDict[tuple(np.sort([target,x]))] for x in connectedNodes]
    connectedCentrality =  [centrality[x] for x in connectedNodes]
    targetCentrality = np.full(len(connectedValues),centrality[target])
    
    thisFeatures = np.array([connectedValues,connectedEdge, connectedCentrality,targetCentrality]).T
    preds = list(classifier.predict(thisFeatures))
    
    return max(set(preds), key= preds.count)
    
def naiveClassify(target,G, nodeDict, edgeDict):
    connectedNodes = list(G.neighbors(target))
    preds = list(np.sign([nodeDict[x] for x in connectedNodes]))
    
    connectedNodes = list(G.neighbors(target))
    connectedEdge = [edgeDict[tuple(np.sort([target,x]))] for x in connectedNodes]
    preds = list(np.sign([nodeDict[x] for x in connectedNodes]))
   
    return max(set(preds), key= preds.count)

def accuracy(y,ypred):
    return 1 - (np.sum(np.array(y) != np.array(ypred))/len(y))

In [13]:
values = []
preds = []
naivePreds = []

for i in range(len(trainThreads),len(threads)):
    try:
        thread = getThread(i,data)
        G, nodeDict, edgeDict, centrality = makeGraph(thread)
        y = np.sign(np.array(list(nodeDict.values())))
       
        yPred = [classify(i,G,nodeDict,edgeDict,centrality, clf) for i in nodeDict.keys()]
        naivePred = [naiveClassify(i,G,nodeDict,edgeDict) for i in nodeDict.keys()]
        values.append(y)
        preds.append(yPred)
        naivePreds.append(naivePred) 
    except:
        pass
   
    

C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["P_Date"][i] = convertDate(thread["P_Date"][i][:10])
C:\Users\Le\AppData\Local\Temp\ipykernel_15208\2970843534.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  thread["MemberID"][thread["MemberID"] == members[i]] = index
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

...

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
C:\Users\Le\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\base.py:439: 

In [14]:
y = np.concatenate(values)
yPred = np.concatenate(preds)
yNaivePred = np.concatenate(naivePreds)

In [15]:
accuracy(y,yPred)


0.7953094462540716

In [16]:
accuracy(y,yNaivePred)


0.5843648208469056

### Analysis

In [20]:
def calculateMetrics(actual, predicted):
    n = len(predicted)
    score_dict = {}
    make_text_bold = lambda x: '\033[1m' + x + '\033[0m'

      # Computes confusion matrix
    TN = 0
    TP = 0
    FP = 0
    FN = 0
    for i in range(n):
        if predicted[i] == actual[i]:
            if predicted[i] ==1:
                TP += 1
            else:
                TN += 1
        else:
            if predicted[i] == 1:
                FP += 1
            else:
                FN += 1
    print('Confusion matrix')
    print('         |    positive  | negative  ')
    print(f'positive |  {TN/n}    | {FN/n}  ')
    print(f'negative |  {FP/n}    | {TP/n}  ')
    print('Accuracy: ' + str((TP+TN)/(TP+FP+TN+FN)))
    print('TPR: ' + str(TP/(TP+FN)))
    print('FPR: ' + str(FP/(FP+TN)))
    print('F1-Score ' + str(TP/(TP+.5*(FP+FN))))

In [21]:
calculateMetrics(y, yPred)

Confusion matrix
         |    positive  | negative  
positive |  0.4685342019543974    | 0.10110749185667753  
negative |  0.10358306188925082    | 0.32677524429967425  
Accuracy: 0.7953094462540716
TPR: 0.7637028014616322
FPR: 0.1810521521293555
F1-Score 0.7614999240929102


In [22]:
calculateMetrics(y, yNaivePred)

Confusion matrix
         |    positive  | negative  
positive |  0.31882736156351793    | 0.16599348534201955  
negative |  0.24964169381107493    | 0.2655374592833876  
Accuracy: 0.5843648208469056
TPR: 0.6153381642512077
FPR: 0.4391473756589503
F1-Score 0.5609688962290118
